In [ ]:
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import json
import numpy as np
import scipy as sp
import scipy.stats as st
import scipy.integrate as integrate
from sklearn import linear_model
from sklearn.exceptions import ConvergenceWarning
import statsmodels.api as sm

sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
figsize = (11,6)
legend_fontsize = 16

from matplotlib import rc
rc('font',**{'family':'sans-serif'})
rc('text', usetex=True)
rc('text.latex',preamble=r'\usepackage[utf8]{inputenc}')
rc('text.latex',preamble=r'\usepackage[russian]{babel}')
rc('figure', **{'dpi': 300})

# Байесовский вывод для испытаний Бернулли

In [ ]:
xs = np.arange(-0.5, 1.5, 0.0025)

prior_params = (.15, .15)
experimental_data = (1, 0)

## Априорное распределение
pri = st.beta(prior_params[0], prior_params[1]).pdf
norm_prior = 1
ys_prior = [ pri(x) / norm_prior for x in xs ]

## Правдоподобие
n_heads, n_tails = experimental_data
lk = lambda x : x ** n_heads * (1 - x) ** n_tails
ys_like = [ lk(x) for x in xs ]

## Апостериорное распределение
post = lambda x : lk(x) * pri(x)
norm_post = integrate.quad(lambda x: post(x), 0, 1)[0]
ys_post = [ post(x) / norm_post if x > 0 and x < 1 else 0 for x in xs ]

## И нарисуем
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.plot(xs, ys_prior, linewidth=2, label=r"Априорное распределение")
ax.plot(xs, ys_like, linewidth=2, label=r"Правдоподобие")
ax.plot(xs, ys_post, linewidth=2, label=r"Апостериорное распределение")
ax.set_xlim((-0.5, 1.5))
ax.set_ylim((-0.5, 4.5))
ax.set_xlabel(r"Вероятность орла $\theta$", fontsize=legend_fontsize)
ax.legend(loc="upper left", fontsize=legend_fontsize)
plt.show()

## Hot hand fallacy?

In [ ]:
streak, N, num_experiments = 3, 20, 10000
results, results_streak = [], []
for _ in range(num_experiments):
    x = np.random.randint(2, size=N)
    after_streak = np.array([ i+streak for i in range(N) if np.all(x[i:i+streak] == 1) and (i+streak < N) ])
    if len(after_streak) > 0:
        results_streak.append(np.sum(x[after_streak]) / len(after_streak))
    results.append(np.sum(x) / float(N))

In [ ]:
np.mean(results)

In [ ]:
np.mean(results_streak)

In [ ]:
streak, N, num_experiments = 3, 20, 2000
res = {}
for streak in range(1, 6):
    print("Streak %d..." % streak)
    res[streak] = {}
    for N in [ i for i in range(streak+1, 20)] + [i for i in range(20, 101, 5)]:
        x = np.random.randint(2, size=(num_experiments, N))
        after_streak = [ [i+streak for i in range(N) if np.all(x[j,i:i+streak] == 1) and (i+streak < N)] for j in range(num_experiments) ]
        after_streak_avg = [ np.mean(x[j,a]) for (j,a) in enumerate(after_streak) if len(a) > 0 ]
        res[streak][N] = np.mean(after_streak_avg)

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
for streak in range(1, 6):
    xs = sorted(res[streak].keys())
    ax.plot(xs, [res[streak][x] for x in xs], linewidth=2, label="После %d орл" % streak + ("а" if streak == 1 else "ов"))
ax.set_xlim((0, 100))
ax.set_ylim((.3, 0.5))
ax.legend(loc="lower right", ncol=3, fontsize=legend_fontsize)
plt.show()